In [2]:
import os
import numpy as np
import pyedflib
from sklearn import svm
from sklearn.metrics import accuracy_score
from scipy.signal import welch, coherence
from pywt import wavedec
from mne.time_frequency import psd_array_multitaper
from scipy.stats import skew, kurtosis
from sklearn.model_selection import GridSearchCV
import mne
def extract_features(file):
    # Read the EDF file using the mne library.
    raw = mne.io.read_raw_edf(file, preload=True)
    
    # Set the channel types.
    raw.set_channel_types({ch: 'eeg' for ch in raw.ch_names})
    
    # Apply a bandpass filter to the EEG data.
    raw.filter(0.5, 45)
    
    # Get the data from the Raw object.
    sigbufs = raw.get_data()
    
    # Set the sampling frequency.
    fs = int(raw.info['sfreq'])
    
    # Set the frequency bands.
    bands = [(0.5, 4), (4, 8), (8, 12), (12, 30), (30, 45)]
    
    # Generate statistical features
    features = []
    for signal in sigbufs:
        features.append(np.mean(signal))
        features.append(np.std(signal))
        features.append(np.min(signal))
        features.append(np.max(signal))
        features.append(skew(signal))
        features.append(kurtosis(signal))
        
        # Calculate the PSD using multitaper method
        f, Pxx = psd_array_multitaper(signal, fs)
        
        # Calculate the total power
        total_power = np.sum(Pxx)
        
        # Calculate the power in each frequency band
        band_power = []
        for band in bands:
            mask = (f >= band[0]) & (f < band[1])
            band_power.append(np.sum(Pxx[mask]) / total_power)
        
        # Append the band power values to the feature vector
        features.extend(band_power)
        
        # Apply a wavelet transform to decompose the signal into different frequency bands
        coeffs = wavedec(signal, 'db4', level=5)
        
        # Extract statistical measures from the wavelet coefficients
        for coeff in coeffs:
            features.append(np.mean(coeff))
            features.append(np.std(coeff))
            features.append(np.min(coeff))
            features.append(np.max(coeff))
            features.append(skew(coeff))
            features.append(kurtosis(coeff))
    
    # Calculate the coherence between all pairs of EEG channels
    for i in range(sigbufs.shape[0]):
        for j in range(i + 1, sigbufs.shape[0]):
            f, Cxy = coherence(sigbufs[i], sigbufs[j], fs=fs)
            features.extend(Cxy)
    
    return features



def train_and_evaluate_svm(X_train, y_train, X_test, y_test):
    # Train an SVM classifier on the training data.
    clf = svm.SVC()
    clf.fit(X_train, y_train)

    # Make predictions on the test data.
    y_pred = clf.predict(X_test)

    # Calculate the accuracy of the classifier.
    accuracy = accuracy_score(y_test, y_pred)

    # Return the trained classifier and the accuracy.
    return clf, accuracy

if __name__ == "__main__":
    # Set the path to the directory where the subject folders are located.
    data_dir = "C:/aditya/Research_Intership/eeg_files/files"
    # Set the number of subjects and the number of runs per subject.
    n_subjects = 109
    n_runs = 14

    # Set the number of baseline runs.
    n_baseline_runs = 2

    # Set the training and test runs.
    training_runs = list(range(n_baseline_runs + 1, n_baseline_runs + 9))
    test_runs = list(range(n_baseline_runs + 9, n_runs + 1))

    # Initialize the training feature matrix and label vector.
    X_train = []
    y_train = []

    # Initialize the test feature matrix and label vector.
    X_test = []
    y_test = []

    # Loop over all subjects.
    for subject in range(1, n_subjects + 1):
        # Set the subject folder name.
        subject_folder = os.path.join(data_dir, f"S{subject:03d}")

        # Loop over all runs.
        for run in range(1, n_runs + 1):
            # Set the file name.
            file_name = os.path.join(subject_folder, f"S{subject:03d}R{run:02d}.edf")

            # Extract the features from the EDF file.
            features = extract_features(file_name)

            # Check if this is a baseline run, a training run, or a test run.
            if run <= n_baseline_runs:
                continue
            elif run in training_runs:
                # Append the features to the training feature matrix.
                X_train.append(features)

                # Append the subject ID to the training label vector.
                y_train.append(subject)
            elif run in test_runs:
                # Append the features to the test feature matrix.
                X_test.append(features)

                # Append the subject ID to the test label vector.
                y_test.append(subject)

    # Convert the feature matrices and label vectors to NumPy arrays.
    X_train = np.array(X_train)
    y_train = np.array(y_train)
    X_test = np.array(X_test)
    y_test = np.array(y_test)

    # Train and evaluate an SVM classifier on the data.
    clf, accuracy = train_and_evaluate_svm(X_train, y_train, X_test, y_test)

    # Print the accuracy of the classifier.
    print(f"Accuracy: {accuracy:.2f}")

Extracting EDF parameters from C:\aditya\Research_Intership\eeg_files\files\S001\S001R01.edf...
EDF file detected
Setting channel info structure...
Creating raw.info structure...
Reading 0 ... 9759  =      0.000 ...    60.994 secs...
Filtering raw data in 1 contiguous segment
Setting up band-pass filter from 0.5 - 45 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 0.50
- Lower transition bandwidth: 0.50 Hz (-6 dB cutoff frequency: 0.25 Hz)
- Upper passband edge: 45.00 Hz
- Upper transition bandwidth: 11.25 Hz (-6 dB cutoff frequency: 50.62 Hz)
- Filter length: 1057 samples (6.606 sec)

    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multita

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s


    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spe

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s


    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spe

...

    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spe

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s


    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spe

[Parallel(n_jobs=1)]: Done  17 tasks      | elapsed:    0.0s


    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spectrum estimation with 7 DPSS windows
    Using multitaper spe

In [7]:
import pandas as pd  
import numpy as np  
from sklearn.svm import SVC  
from sklearn.metrics import classification_report, confusion_matrix  
import matplotlib.pyplot as plt